In [2]:
import warnings
warnings.filterwarnings('ignore')
import glob
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from lightgbm import LGBMClassifier
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import OneHotEncoder
import random
import os
from sklearn.metrics import log_loss


d = "C:\kaggle_data\credit_card"

train = pd.read_csv(d + '\\' +'train.csv')
test = pd.read_csv(d + '\\' +'test.csv')
ss = pd.read_csv(d + '\\' +'sample_submission.csv')
train = train.drop(['index'], axis=1)
train.fillna('NAN', inplace=True) 
test = test.drop(['index'], axis=1)
test.fillna('NAN', inplace=True)

y = train.pop('credit')

def simple_pp(train, test):
    
    # Married, Civil marriage
    train['income_per_size'] = np.log(train['income_total']/train['family_size'])
    test['income_per_size'] = np.log(test['income_total']/test['family_size'])
    train.loc[(train['family_type']=='Married')|(train['family_type']=='Civil marriage'),'income_per_size']\
    = train['income_per_size'] * 2
    test.loc[(test['family_type']=='Married')|(test['family_type']=='Civil marriage'),'income_per_size']\
    = test['income_per_size'] * 2
    
    train['gender'] =train['gender'].apply(lambda x: int(x=='F'))
    test['gender'] =test['gender'].apply(lambda x: int(x=='F'))
    
    
    def simple_marry(x):
        if x == 'Married' or x =='Civil marriage':
            return '0'
        elif x == 'Separated' or x == 'Widow':
            return '1'
        else:
            return '2'

    for df in [train,test]:
        df['family_bins'] = df['family_type'].apply(simple_marry)

    # car와 reality를 합친 새로운 칼럼 careality
    train['car'] =train['car'].apply(lambda x: int(x=='Y'))
    train['reality'] =train['reality'].apply(lambda x: int(x=='Y'))
    test['car'] =test['car'].apply(lambda x: int(x=='Y'))
    test['reality'] =test['reality'].apply(lambda x: int(x=='Y'))

    train['careality'] = train['car'] + train['reality']
    train = train.drop(['car', 'reality'],1)

    test['careality'] = test['car'] + test['reality']
    test = test.drop(['car', 'reality'],1)



    object_col = []
    for col in train.columns:
        if train[col].dtype == 'object':
            object_col.append(col)

    enc = OneHotEncoder()
    enc.fit(train.loc[:,object_col])


    train_onehot_df = pd.DataFrame(enc.transform(train.loc[:,object_col]).toarray(), 
                 columns=enc.get_feature_names(object_col))
    train.drop(object_col, axis=1, inplace=True)
    train = pd.concat([train, train_onehot_df], axis=1)

    test_onehot_df = pd.DataFrame(enc.transform(test.loc[:,object_col]).toarray(), 
                 columns=enc.get_feature_names(object_col))
    test.drop(object_col, axis=1, inplace=True)
    test = pd.concat([test, test_onehot_df], axis=1)

    ## 제곱
    for df in [train,test]:
        df['income_per_size'] = df['income_per_size'].apply(lambda x: x**2)
    
    return train,test

def log_pp(train,test):
    
    # Married, Civil marriage
    train['income_per_size'] = np.log(train['income_total']/train['family_size'])
    test['income_per_size'] = np.log(test['income_total']/test['family_size'])
    train.loc[(train['family_type']=='Married')|(train['family_type']=='Civil marriage'),'income_per_size']\
    = train['income_per_size'] * 2
    test.loc[(test['family_type']=='Married')|(test['family_type']=='Civil marriage'),'income_per_size']\
    = test['income_per_size'] * 2

    def simple_marry(x):
        if x == 'Married' or x =='Civil marriage':
            return '0'
        elif x == 'Separated' or x == 'Widow':
            return '1'
        else:
            return '2'

    for df in [train,test]:
        df['family_bins'] = df['family_type'].apply(simple_marry)

    # car와 reality를 합친 새로운 칼럼 careality
    train['car'] =train['car'].apply(lambda x: int(x=='Y'))
    train['reality'] =train['reality'].apply(lambda x: int(x=='Y'))
    test['car'] =test['car'].apply(lambda x: int(x=='Y'))
    test['reality'] =test['reality'].apply(lambda x: int(x=='Y'))

    train['careality'] = train['car'] + train['reality']
    train = train.drop(['car', 'reality'],1)

    test['careality'] = test['car'] + test['reality']
    test = test.drop(['car', 'reality'],1)



    object_col = []
    for col in train.columns:
        if train[col].dtype == 'object':
            object_col.append(col)

    enc = OneHotEncoder()
    enc.fit(train.loc[:,object_col])


    train_onehot_df = pd.DataFrame(enc.transform(train.loc[:,object_col]).toarray(), 
                 columns=enc.get_feature_names(object_col))
    train.drop(object_col, axis=1, inplace=True)
    train = pd.concat([train, train_onehot_df], axis=1)

    test_onehot_df = pd.DataFrame(enc.transform(test.loc[:,object_col]).toarray(), 
                 columns=enc.get_feature_names(object_col))
    test.drop(object_col, axis=1, inplace=True)
    test = pd.concat([test, test_onehot_df], axis=1)

    ## 제곱
    for df in [train,test]:
        df['income_per_size'] = df['income_per_size'].apply(lambda x: x**2)
    
    
    log_cols = ['income_per_size', 'income_total', 'begin_month','DAYS_BIRTH']
    
    for col in log_cols:
        train[col] = np.log1p(train[col].abs())
        test[col] = np.log1p(test[col].abs())
    
    
    train['DAYS_EMPLOYED'] = train['DAYS_EMPLOYED'].abs()
    test['DAYS_EMPLOYED'] = test['DAYS_EMPLOYED'].abs()
        
    m = train['DAYS_EMPLOYED'].mean()
    s = train['DAYS_EMPLOYED'].std()
        
    for df in [train,test]:        
        df['DAYS_EMPLOYED'] = (df['DAYS_EMPLOYED']-m)/s
        
    return train, test

def scale_pp(train,test):
    
    # Married, Civil marriage
    train['income_per_size'] = np.log(train['income_total']/train['family_size'])
    test['income_per_size'] = np.log(test['income_total']/test['family_size'])
    train.loc[(train['family_type']=='Married')|(train['family_type']=='Civil marriage'),'income_per_size']\
    = train['income_per_size'] * 2
    test.loc[(test['family_type']=='Married')|(test['family_type']=='Civil marriage'),'income_per_size']\
    = test['income_per_size'] * 2

    def simple_marry(x):
        if x == 'Married' or x =='Civil marriage':
            return '0'
        elif x == 'Separated' or x == 'Widow':
            return '1'
        else:
            return '2'

    for df in [train,test]:
        df['family_bins'] = df['family_type'].apply(simple_marry)

    # income_total을 로그변환
    train['income_total'] = np.log(train['income_total'])
    test['income_total'] = np.log(test['income_total'])


    # car와 reality를 합친 새로운 칼럼 careality
    train['car'] =train['car'].apply(lambda x: int(x=='Y'))
    train['reality'] =train['reality'].apply(lambda x: int(x=='Y'))
    test['car'] =test['car'].apply(lambda x: int(x=='Y'))
    test['reality'] =test['reality'].apply(lambda x: int(x=='Y'))

    train['careality'] = train['car'] + train['reality']
    train = train.drop(['car', 'reality'],1)

    test['careality'] = test['car'] + test['reality']
    test = test.drop(['car', 'reality'],1)



    object_col = []
    for col in train.columns:
        if train[col].dtype == 'object':
            object_col.append(col)

    enc = OneHotEncoder()
    enc.fit(train.loc[:,object_col])


    train_onehot_df = pd.DataFrame(enc.transform(train.loc[:,object_col]).toarray(), 
                 columns=enc.get_feature_names(object_col))
    train.drop(object_col, axis=1, inplace=True)
    train = pd.concat([train, train_onehot_df], axis=1)

    test_onehot_df = pd.DataFrame(enc.transform(test.loc[:,object_col]).toarray(), 
                 columns=enc.get_feature_names(object_col))
    test.drop(object_col, axis=1, inplace=True)
    test = pd.concat([test, test_onehot_df], axis=1)

    ## 제곱
    for df in [train,test]:
        df['income_per_size'] = df['income_per_size'].apply(lambda x: x**2)
    
    
    scale_cols = ['income_per_size', 'income_total', 'begin_month','DAYS_BIRTH','DAYS_EMPLOYED']
    
    for col in scale_cols:
        m = train[col].mean()
        s = train[col].std()
        
        train[col] = (train[col]-m)/s
        test[col] = (test[col]-m)/s
        
    return train, test

In [6]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import GaussianNB
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import ExtraTreesClassifier
import keras
# from keras import models
from keras import layers
from sklearn.svm import SVC


forest = RandomForestClassifier(n_estimators = 1000, 
                                    max_depth = 300, 
                                    min_samples_leaf = 2, 
                                    min_samples_split = 6,
                                    max_features = 9)

nb = GaussianNB()

xgboost = XGBClassifier(tree_method = "gpu_hist",
                        n_estimators = 700,
                        max_depth = 25,
                        learning_rate= 0.1,
                        min_child_weight = 2,
                        subsample = 0.85,
                        colsample_bytree = 0.31,
                        gamma = 0,
                        max_delta_step = 0.07,
                        nthread = -1,
                        eval_metric = 'mlogloss')





lightgbm = LGBMClassifier(boosting_type='gbdt',
                          objective='multiclass',
                          n_estimators=1000,
                          max_depth = 9,
                          subsample=0.9,
                          subsample_freq=2,
                          colsample_bytree=0.7,
                          n_jobs=-1,
                          metric = 'multi_logloss')



adaboost = AdaBoostClassifier(n_estimators=1000)

extratree = ExtraTreesClassifier(n_estimators=1000)

nn = keras.models.Sequential()
es = keras.callbacks.EarlyStopping(monitor='sparse_categorical_crossentropy',patience=50)

svm = SVC(probability=True)



knn_1 = KNeighborsClassifier(n_neighbors = 1, metric='euclidean', weights='distance')
knn_2 = KNeighborsClassifier(n_neighbors = 2, metric='euclidean', weights='distance')
knn_4 = KNeighborsClassifier(n_neighbors = 4, metric='euclidean', weights='distance')
knn_8 = KNeighborsClassifier(n_neighbors = 8, metric='euclidean', weights='distance')
knn_16 = KNeighborsClassifier(n_neighbors = 16, metric='euclidean', weights='distance')
knn_32 = KNeighborsClassifier(n_neighbors = 32, metric='euclidean', weights='distance')
knn_64 = KNeighborsClassifier(n_neighbors = 64, metric='euclidean', weights='distance')
knn_128 = KNeighborsClassifier(n_neighbors = 128, metric='euclidean', weights='distance')
knn_256 = KNeighborsClassifier(n_neighbors = 256, metric='euclidean', weights='distance')
knn_512 = KNeighborsClassifier(n_neighbors = 512, metric='euclidean', weights='distance')
knn_1024 = KNeighborsClassifier(n_neighbors = 1024, metric='euclidean', weights='distance')


models = [forest, nb, xgboost, lightgbm, adaboost, extratree, nn, svm,\
          knn_1, knn_2, knn_4, knn_8, knn_16, knn_32, knn_64, knn_128, knn_256, knn_512, knn_1024]


# take_1 = [forest, nb, xgboost, adaboost, extratree, nn]

# take_2 = [lightgbm, svm]

# take_3 = [knn_1, knn_2, knn_4, knn_8, knn_16]

# take_4 = [knn_32, knn_64, knn_128, knn_256]

# take_5 = [knn_512, knn_1024]



### ver1. adaboost, extratree, knn        # 원래 데이터 옆에 concat
### ver2. ver1을 2번 돌린 거  csv

### train 학습 a
### train + a 학습

In [3]:
def oof_train(model,X, y, test):
    """
    모델, X, y, test를 넣어주면
    oof로 만든 새로운 train과 test셋의 앙상블 결과를 반환
    
    X_oof: train을 oof로 학습, 예측하여 만든 새로운 train set
    test_oof: skf로 학습한 총 10개의 모델 결과를 soft voting
    """
    if model != nn:
    
        skf = StratifiedKFold(n_splits=10, shuffle=False)
        X_oof = np.zeros(y.shape)
        ss = np.zeros((10000,3))
    #     y_test = np.zeros(())
        for train_idx, valid_idx in skf.split(X, y):
            X_train, y_train = X.iloc[train_idx,:], y[train_idx]
            X_valid, y_valid = X.iloc[valid_idx,:], y[valid_idx]

            model.fit(X_train, y_train)
            X_oof[valid_idx] += model.predict(X.iloc[valid_idx])

            ss += model.predict_proba(test)

        test_oof = np.argmax(ss,1)


        return X_oof, test_oof
    
    
    elif model == nn:
        
        skf = StratifiedKFold(n_splits=10, shuffle=False)
        X_oof = np.zeros(y.shape)
        ss = np.zeros((10000,3))
    
    
        for train_idx, valid_idx in skf.split(X, y):
            X_train, y_train = X.iloc[train_idx,:].values, y[train_idx].values
            X_valid, y_valid = X.iloc[valid_idx,:].values, y[valid_idx].values
            
            input_shape = len(X.columns)
            model = keras.models.Sequential()
            model.add(layers.Dense(16, activation='relu', input_shape=(input_shape,)))
            model.add(layers.Dense(8,activation='relu'))
            model.add(layers.Dense(3,activation='softmax'))

            model.compile(optimizer='rmsprop',
                             loss='sparse_categorical_crossentropy',
                             metrics=['acc'])
            model.fit(x = X_train, 
                        y = y_train,
                       epochs=10000,
                        batch_size=98304,
                       validation_data =(X_valid, y_valid),
                           verbose=100,
                           callbacks=[es])


            X_oof[valid_idx] += np.argmax(model.predict(X.iloc[valid_idx].values),1)
            ss += model.predict_proba(x_test.values)

        test_oof = np.argmax(ss,1)
        return X_oof, test_oof

In [4]:
x_train, x_test = simple_pp(train, test)

# 연속형 로그 변환
x_train_log, x_test_log = log_pp(train, test)

# 연속형 표준화
x_train_scale, x_test_scale = scale_pp(train,test)

In [ ]:
# 1:30시작?
# 5:58 15 fold
trains = [x_train, x_train_log, x_train_scale]
tests = [x_test, x_test_log, x_test_scale]
columns = []

train_lv0 = []
test_lv0 = []
for model in models:
    cnt = 0
    model_name = str(model).split('(')[0]
    for X, test in zip(trains, tests):
        print(f'{model_name}의 {cnt+1}번째 학습중')
        col_name = str(model).split('(')[0]+'_'+str(cnt+1)
        
        X_oof, test_oof = oof_train(model, X, y, test)
        train_lv0.append(X_oof)
        test_lv0.append(test_oof)
        columns.append(col_name)
        cnt += 1

LGBMClassifier의 1번째 학습중
LGBMClassifier의 2번째 학습중
LGBMClassifier의 3번째 학습중
SVC의 1번째 학습중


In [81]:
train_0 = pd.DataFrame(np.array(train_lv0).T, columns=columns)

In [82]:
test_0 = pd.DataFrame(np.array(test_lv0).T, columns=columns)

In [39]:
train_orig = pd.read_csv(d + '\\' +'train.csv')
test_orig = pd.read_csv(d + '\\' +'test.csv')

train_orig.fillna('NAN', inplace=True)
test_orig.fillna('NAN', inplace=True)

In [40]:
train_take_1 = pd.read_csv('train_take_1.csv')
train_take_2 = pd.read_csv('train_take_2.csv')
train_take_3 = pd.read_csv('train_take_3.csv')
train_take_4 = pd.read_csv('train_take_4.csv')
train_take_5 = pd.read_csv('train_take_5.csv')

test_take_1= pd.read_csv('test_take_1.csv')
test_take_2= pd.read_csv('test_take_2.csv')
test_take_3= pd.read_csv('test_take_3.csv')
test_take_4= pd.read_csv('test_take_4.csv')
test_take_5= pd.read_csv('test_take_5.csv')

In [41]:
new_train = pd.concat([train_take_1,train_take_2,train_take_3,train_take_4,train_take_5],1)
new_test = pd.concat([test_take_1,test_take_2,test_take_3,test_take_4,test_take_5],1)

In [43]:
train_ver1 = pd.concat([train_orig,new_train,y],1)
test_ver1 = pd.concat([test_orig,new_test],1)

In [46]:
train_ver1.to_csv('train_ver1.csv',index=False)
test_ver1.to_csv('test_ver1.csv',index=False)

In [23]:
import keras
from keras import models
from keras import layers




X = 
test = 





es = keras.callbacks.EarlyStopping(monitor='sparse_categorical_crossentropy',patience=50)
skf = StratifiedKFold(n_splits=10, shuffle=False)
nn = np.zeros((10000,3))

for i, (train_idx, valid_idx) in enumerate(skf.split(X,y)):    
    
    X_train, y_train = X.iloc[train_idx,:], y[train_idx]
    X_valid, y_valid = X.iloc[valid_idx,:], y[valid_idx]
    
    model = models.Sequential()
    model.add(layers.Dense(16, activation='relu', input_shape=(18,)))
    model.add(layers.Dense(8,activation='relu'))
    model.add(layers.Dense(3,activation='softmax'))

    model.compile(optimizer='rmsprop',
                     loss='sparse_categorical_crossentropy',
                     metrics=['acc'])
    model.fit(x = X_train, 
                y = y_train,
               epochs=10000,
                batch_size=98304,
               validation_data =(X_valid, y_valid),
                   verbose=100,
                   callbacks=[es])
    
    nn += model.predict_proba(test)/10

Train on 23811 samples, validate on 2646 samples
Epoch 1/10000
Epoch 2/10000
Epoch 3/10000
Epoch 4/10000
Epoch 5/10000
Epoch 6/10000
Epoch 7/10000
Epoch 8/10000
Epoch 9/10000
Epoch 10/10000
Epoch 11/10000
Epoch 12/10000
Epoch 13/10000
Epoch 14/10000
Epoch 15/10000
Epoch 16/10000
Epoch 17/10000
Epoch 18/10000
Epoch 19/10000
Epoch 20/10000
Epoch 21/10000
Epoch 22/10000
Epoch 23/10000
Epoch 24/10000
Epoch 25/10000
Epoch 26/10000
Epoch 27/10000
Epoch 28/10000
Epoch 29/10000
Epoch 30/10000
Epoch 31/10000
Epoch 32/10000
Epoch 33/10000
Epoch 34/10000
Epoch 35/10000
Epoch 36/10000
Epoch 37/10000
Epoch 38/10000
Epoch 39/10000
Epoch 40/10000
Epoch 41/10000
Epoch 42/10000
Epoch 43/10000
Epoch 44/10000
Epoch 45/10000
Epoch 46/10000
Epoch 47/10000
Epoch 48/10000
Epoch 49/10000
Epoch 50/10000
Epoch 51/10000
Epoch 52/10000
Epoch 53/10000
Epoch 54/10000
Epoch 55/10000
Epoch 56/10000
Epoch 57/10000
Epoch 58/10000
Epoch 59/10000
Epoch 60/10000
Epoch 61/10000
Epoch 62/10000
Epoch 63/10000
Epoch 64/10000


Epoch 520/10000
Epoch 521/10000
Epoch 522/10000
Epoch 523/10000
Epoch 524/10000
Epoch 525/10000
Epoch 526/10000
Epoch 527/10000
Epoch 528/10000
Epoch 529/10000
Epoch 530/10000
Epoch 531/10000
Epoch 532/10000
Epoch 533/10000
Epoch 534/10000
Epoch 535/10000
Epoch 536/10000
Epoch 537/10000
Epoch 538/10000
Epoch 539/10000
Epoch 540/10000
Epoch 541/10000
Epoch 542/10000
Epoch 543/10000
Epoch 544/10000
Epoch 545/10000
Epoch 546/10000
Epoch 547/10000
Epoch 548/10000
Epoch 549/10000
Epoch 550/10000
Epoch 551/10000
Epoch 552/10000
Epoch 553/10000
Epoch 554/10000
Epoch 555/10000
Epoch 556/10000
Epoch 557/10000
Epoch 558/10000
Epoch 559/10000
Epoch 560/10000
Epoch 561/10000
Epoch 562/10000
Epoch 563/10000
Epoch 564/10000
Epoch 565/10000
Epoch 566/10000
Epoch 567/10000
Epoch 568/10000
Epoch 569/10000
Epoch 570/10000
Epoch 571/10000
Epoch 572/10000
Epoch 573/10000
Epoch 574/10000
Epoch 575/10000
Epoch 576/10000
Epoch 577/10000
Epoch 578/10000
Epoch 579/10000
Epoch 580/10000
Epoch 581/10000
Epoch 58

Epoch 1034/10000
Epoch 1035/10000
Epoch 1036/10000
Epoch 1037/10000
Epoch 1038/10000
Epoch 1039/10000
Epoch 1040/10000
Epoch 1041/10000
Epoch 1042/10000
Epoch 1043/10000
Epoch 1044/10000
Epoch 1045/10000
Epoch 1046/10000
Epoch 1047/10000
Epoch 1048/10000
Epoch 1049/10000
Epoch 1050/10000
Epoch 1051/10000
Epoch 1052/10000
Epoch 1053/10000
Epoch 1054/10000
Epoch 1055/10000
Epoch 1056/10000
Epoch 1057/10000
Epoch 1058/10000
Epoch 1059/10000
Epoch 1060/10000
Epoch 1061/10000
Epoch 1062/10000
Epoch 1063/10000
Epoch 1064/10000
Epoch 1065/10000
Epoch 1066/10000
Epoch 1067/10000
Epoch 1068/10000
Epoch 1069/10000
Epoch 1070/10000
Epoch 1071/10000
Epoch 1072/10000
Epoch 1073/10000
Epoch 1074/10000
Epoch 1075/10000
Epoch 1076/10000
Epoch 1077/10000
Epoch 1078/10000
Epoch 1079/10000
Epoch 1080/10000
Epoch 1081/10000
Epoch 1082/10000
Epoch 1083/10000
Epoch 1084/10000
Epoch 1085/10000
Epoch 1086/10000
Epoch 1087/10000
Epoch 1088/10000
Epoch 1089/10000
Epoch 1090/10000
Epoch 1091/10000
Epoch 1092/100

Epoch 1529/10000
Epoch 1530/10000
Epoch 1531/10000
Epoch 1532/10000
Epoch 1533/10000
Epoch 1534/10000
Epoch 1535/10000
Epoch 1536/10000
Epoch 1537/10000
Epoch 1538/10000
Epoch 1539/10000
Epoch 1540/10000
Epoch 1541/10000
Epoch 1542/10000
Epoch 1543/10000
Epoch 1544/10000
Epoch 1545/10000
Epoch 1546/10000
Epoch 1547/10000
Epoch 1548/10000
Epoch 1549/10000
Epoch 1550/10000
Epoch 1551/10000
Epoch 1552/10000
Epoch 1553/10000
Epoch 1554/10000
Epoch 1555/10000
Epoch 1556/10000
Epoch 1557/10000
Epoch 1558/10000
Epoch 1559/10000
Epoch 1560/10000
Epoch 1561/10000
Epoch 1562/10000
Epoch 1563/10000
Epoch 1564/10000
Epoch 1565/10000
Epoch 1566/10000
Epoch 1567/10000
Epoch 1568/10000
Epoch 1569/10000
Epoch 1570/10000
Epoch 1571/10000
Epoch 1572/10000
Epoch 1573/10000
Epoch 1574/10000
Epoch 1575/10000
Epoch 1576/10000
Epoch 1577/10000
Epoch 1578/10000
Epoch 1579/10000
Epoch 1580/10000
Epoch 1581/10000
Epoch 1582/10000
Epoch 1583/10000
Epoch 1584/10000
Epoch 1585/10000
Epoch 1586/10000
Epoch 1587/100

Epoch 2021/10000
Epoch 2022/10000
Epoch 2023/10000
Epoch 2024/10000
Epoch 2025/10000
Epoch 2026/10000
Epoch 2027/10000
Epoch 2028/10000
Epoch 2029/10000
Epoch 2030/10000
Epoch 2031/10000
Epoch 2032/10000
Epoch 2033/10000
Epoch 2034/10000
Epoch 2035/10000
Epoch 2036/10000
Epoch 2037/10000
Epoch 2038/10000
Epoch 2039/10000
Epoch 2040/10000
Epoch 2041/10000
Epoch 2042/10000
Epoch 2043/10000
Epoch 2044/10000
Epoch 2045/10000
Epoch 2046/10000
Epoch 2047/10000
Epoch 2048/10000
Epoch 2049/10000
Epoch 2050/10000
Epoch 2051/10000
Epoch 2052/10000
Epoch 2053/10000
Epoch 2054/10000
Epoch 2055/10000
Epoch 2056/10000
Epoch 2057/10000
Epoch 2058/10000
Epoch 2059/10000
Epoch 2060/10000
Epoch 2061/10000
Epoch 2062/10000
Epoch 2063/10000
Epoch 2064/10000
Epoch 2065/10000
Epoch 2066/10000
Epoch 2067/10000
Epoch 2068/10000
Epoch 2069/10000
Epoch 2070/10000
Epoch 2071/10000
Epoch 2072/10000
Epoch 2073/10000
Epoch 2074/10000
Epoch 2075/10000
Epoch 2076/10000
Epoch 2077/10000
Epoch 2078/10000
Epoch 2079/100

...

Epoch 7898/10000
Epoch 7899/10000
Epoch 7900/10000
Epoch 7901/10000
Epoch 7902/10000
Epoch 7903/10000
Epoch 7904/10000
Epoch 7905/10000
Epoch 7906/10000
Epoch 7907/10000
Epoch 7908/10000
Epoch 7909/10000
Epoch 7910/10000
Epoch 7911/10000
Epoch 7912/10000
Epoch 7913/10000
Epoch 7914/10000
Epoch 7915/10000
Epoch 7916/10000
Epoch 7917/10000
Epoch 7918/10000
Epoch 7919/10000
Epoch 7920/10000
Epoch 7921/10000
Epoch 7922/10000
Epoch 7923/10000
Epoch 7924/10000
Epoch 7925/10000
Epoch 7926/10000
Epoch 7927/10000
Epoch 7928/10000
Epoch 7929/10000
Epoch 7930/10000
Epoch 7931/10000
Epoch 7932/10000
Epoch 7933/10000
Epoch 7934/10000
Epoch 7935/10000
Epoch 7936/10000
Epoch 7937/10000
Epoch 7938/10000
Epoch 7939/10000
Epoch 7940/10000
Epoch 7941/10000
Epoch 7942/10000
Epoch 7943/10000
Epoch 7944/10000
Epoch 7945/10000
Epoch 7946/10000
Epoch 7947/10000
Epoch 7948/10000
Epoch 7949/10000
Epoch 7950/10000
Epoch 7951/10000
Epoch 7952/10000
Epoch 7953/10000
Epoch 7954/10000
Epoch 7955/10000
Epoch 7956/100

Epoch 8393/10000
Epoch 8394/10000
Epoch 8395/10000
Epoch 8396/10000
Epoch 8397/10000
Epoch 8398/10000
Epoch 8399/10000
Epoch 8400/10000
Epoch 8401/10000
Epoch 8402/10000
Epoch 8403/10000
Epoch 8404/10000
Epoch 8405/10000
Epoch 8406/10000
Epoch 8407/10000
Epoch 8408/10000
Epoch 8409/10000
Epoch 8410/10000
Epoch 8411/10000
Epoch 8412/10000
Epoch 8413/10000
Epoch 8414/10000
Epoch 8415/10000
Epoch 8416/10000
Epoch 8417/10000
Epoch 8418/10000
Epoch 8419/10000
Epoch 8420/10000
Epoch 8421/10000
Epoch 8422/10000
Epoch 8423/10000
Epoch 8424/10000
Epoch 8425/10000
Epoch 8426/10000
Epoch 8427/10000
Epoch 8428/10000
Epoch 8429/10000
Epoch 8430/10000
Epoch 8431/10000
Epoch 8432/10000
Epoch 8433/10000
Epoch 8434/10000
Epoch 8435/10000
Epoch 8436/10000
Epoch 8437/10000
Epoch 8438/10000
Epoch 8439/10000
Epoch 8440/10000
Epoch 8441/10000
Epoch 8442/10000
Epoch 8443/10000
Epoch 8444/10000
Epoch 8445/10000
Epoch 8446/10000
Epoch 8447/10000
Epoch 8448/10000
Epoch 8449/10000
Epoch 8450/10000
Epoch 8451/100

Epoch 8875/10000
Epoch 8876/10000
Epoch 8877/10000
Epoch 8878/10000
Epoch 8879/10000
Epoch 8880/10000
Epoch 8881/10000
Epoch 8882/10000
Epoch 8883/10000
Epoch 8884/10000
Epoch 8885/10000
Epoch 8886/10000
Epoch 8887/10000
Epoch 8888/10000
Epoch 8889/10000
Epoch 8890/10000
Epoch 8891/10000
Epoch 8892/10000
Epoch 8893/10000
Epoch 8894/10000
Epoch 8895/10000
Epoch 8896/10000
Epoch 8897/10000
Epoch 8898/10000
Epoch 8899/10000
Epoch 8900/10000
Epoch 8901/10000
Epoch 8902/10000
Epoch 8903/10000
Epoch 8904/10000
Epoch 8905/10000
Epoch 8906/10000
Epoch 8907/10000
Epoch 8908/10000
Epoch 8909/10000
Epoch 8910/10000
Epoch 8911/10000
Epoch 8912/10000
Epoch 8913/10000
Epoch 8914/10000
Epoch 8915/10000
Epoch 8916/10000
Epoch 8917/10000
Epoch 8918/10000
Epoch 8919/10000
Epoch 8920/10000
Epoch 8921/10000
Epoch 8922/10000
Epoch 8923/10000
Epoch 8924/10000
Epoch 8925/10000
Epoch 8926/10000
Epoch 8927/10000
Epoch 8928/10000
Epoch 8929/10000
Epoch 8930/10000
Epoch 8931/10000
Epoch 8932/10000
Epoch 8933/100

Epoch 9363/10000
Epoch 9364/10000
Epoch 9365/10000
Epoch 9366/10000
Epoch 9367/10000
Epoch 9368/10000
Epoch 9369/10000
Epoch 9370/10000
Epoch 9371/10000
Epoch 9372/10000
Epoch 9373/10000
Epoch 9374/10000
Epoch 9375/10000
Epoch 9376/10000
Epoch 9377/10000
Epoch 9378/10000
Epoch 9379/10000
Epoch 9380/10000
Epoch 9381/10000
Epoch 9382/10000
Epoch 9383/10000
Epoch 9384/10000
Epoch 9385/10000
Epoch 9386/10000
Epoch 9387/10000
Epoch 9388/10000
Epoch 9389/10000
Epoch 9390/10000
Epoch 9391/10000
Epoch 9392/10000
Epoch 9393/10000
Epoch 9394/10000
Epoch 9395/10000
Epoch 9396/10000
Epoch 9397/10000
Epoch 9398/10000
Epoch 9399/10000
Epoch 9400/10000
Epoch 9401/10000
Epoch 9402/10000
Epoch 9403/10000
Epoch 9404/10000
Epoch 9405/10000
Epoch 9406/10000
Epoch 9407/10000
Epoch 9408/10000
Epoch 9409/10000
Epoch 9410/10000
Epoch 9411/10000
Epoch 9412/10000
Epoch 9413/10000
Epoch 9414/10000
Epoch 9415/10000
Epoch 9416/10000
Epoch 9417/10000
Epoch 9418/10000
Epoch 9419/10000
Epoch 9420/10000
Epoch 9421/100

Epoch 9852/10000
Epoch 9853/10000
Epoch 9854/10000
Epoch 9855/10000
Epoch 9856/10000
Epoch 9857/10000
Epoch 9858/10000
Epoch 9859/10000
Epoch 9860/10000
Epoch 9861/10000
Epoch 9862/10000
Epoch 9863/10000
Epoch 9864/10000
Epoch 9865/10000
Epoch 9866/10000
Epoch 9867/10000
Epoch 9868/10000
Epoch 9869/10000
Epoch 9870/10000
Epoch 9871/10000
Epoch 9872/10000
Epoch 9873/10000
Epoch 9874/10000
Epoch 9875/10000
Epoch 9876/10000
Epoch 9877/10000
Epoch 9878/10000
Epoch 9879/10000
Epoch 9880/10000
Epoch 9881/10000
Epoch 9882/10000
Epoch 9883/10000
Epoch 9884/10000
Epoch 9885/10000
Epoch 9886/10000
Epoch 9887/10000
Epoch 9888/10000
Epoch 9889/10000
Epoch 9890/10000
Epoch 9891/10000
Epoch 9892/10000
Epoch 9893/10000
Epoch 9894/10000
Epoch 9895/10000
Epoch 9896/10000
Epoch 9897/10000
Epoch 9898/10000
Epoch 9899/10000
Epoch 9900/10000
Epoch 9901/10000
Epoch 9902/10000
Epoch 9903/10000
Epoch 9904/10000
Epoch 9905/10000
Epoch 9906/10000
Epoch 9907/10000
Epoch 9908/10000
Epoch 9909/10000
Epoch 9910/100

In [24]:
es = keras.callbacks.EarlyStopping(monitor='sparse_categorical_crossentropy',patience=50)
skf = StratifiedKFold(n_splits=10, shuffle=False)
X = train_0.drop('credit',1)

nn = np.zeros((10000,3))

for i, (train_idx, valid_idx) in enumerate(skf.split(X,y)):    
    
    X_train, y_train = X.iloc[train_idx,:], y[train_idx]
    X_valid, y_valid = X.iloc[valid_idx,:], y[valid_idx]
    
    model = models.Sequential()
    model.add(layers.Dense(16, activation='relu', input_shape=(18,)))
    model.add(layers.Dense(8,activation='relu'))
    model.add(layers.Dense(3,activation='softmax'))

    model.compile(optimizer='rmsprop',
                     loss='sparse_categorical_crossentropy',
                     metrics=['acc'])
    model.fit(x = X_train, 
                y = y_train,
               epochs=10000,
                batch_size=98304,
               validation_data =(X_valid, y_valid),
                   verbose=100,
                   callbacks=[es])
    
    nn += model.predict_proba(test)/10

Train on 23811 samples, validate on 2646 samples
Epoch 1/10000
Epoch 2/10000
Epoch 3/10000
Epoch 4/10000
Epoch 5/10000
Epoch 6/10000
Epoch 7/10000
Epoch 8/10000
Epoch 9/10000
Epoch 10/10000
Epoch 11/10000
Epoch 12/10000
Epoch 13/10000
Epoch 14/10000
Epoch 15/10000
Epoch 16/10000
Epoch 17/10000
Epoch 18/10000
Epoch 19/10000
Epoch 20/10000
Epoch 21/10000
Epoch 22/10000
Epoch 23/10000
Epoch 24/10000
Epoch 25/10000
Epoch 26/10000
Epoch 27/10000
Epoch 28/10000
Epoch 29/10000
Epoch 30/10000
Epoch 31/10000
Epoch 32/10000
Epoch 33/10000
Epoch 34/10000
Epoch 35/10000
Epoch 36/10000
Epoch 37/10000
Epoch 38/10000
Epoch 39/10000
Epoch 40/10000
Epoch 41/10000
Epoch 42/10000
Epoch 43/10000
Epoch 44/10000
Epoch 45/10000
Epoch 46/10000
Epoch 47/10000
Epoch 48/10000
Epoch 49/10000
Epoch 50/10000
Epoch 51/10000
Epoch 52/10000
Epoch 53/10000
Epoch 54/10000
Epoch 55/10000
Epoch 56/10000
Epoch 57/10000
Epoch 58/10000
Epoch 59/10000
Epoch 60/10000
Epoch 61/10000
Epoch 62/10000
Epoch 63/10000
Epoch 64/10000


Epoch 520/10000
Epoch 521/10000
Epoch 522/10000
Epoch 523/10000
Epoch 524/10000
Epoch 525/10000
Epoch 526/10000
Epoch 527/10000
Epoch 528/10000
Epoch 529/10000
Epoch 530/10000
Epoch 531/10000
Epoch 532/10000
Epoch 533/10000
Epoch 534/10000
Epoch 535/10000
Epoch 536/10000
Epoch 537/10000
Epoch 538/10000
Epoch 539/10000
Epoch 540/10000
Epoch 541/10000
Epoch 542/10000
Epoch 543/10000
Epoch 544/10000
Epoch 545/10000
Epoch 546/10000
Epoch 547/10000
Epoch 548/10000
Epoch 549/10000
Epoch 550/10000
Epoch 551/10000
Epoch 552/10000
Epoch 553/10000
Epoch 554/10000
Epoch 555/10000
Epoch 556/10000
Epoch 557/10000
Epoch 558/10000
Epoch 559/10000
Epoch 560/10000
Epoch 561/10000
Epoch 562/10000
Epoch 563/10000
Epoch 564/10000
Epoch 565/10000
Epoch 566/10000
Epoch 567/10000
Epoch 568/10000
Epoch 569/10000
Epoch 570/10000
Epoch 571/10000
Epoch 572/10000
Epoch 573/10000
Epoch 574/10000
Epoch 575/10000
Epoch 576/10000
Epoch 577/10000
Epoch 578/10000
Epoch 579/10000
Epoch 580/10000
Epoch 581/10000
Epoch 58

Epoch 1042/10000
Epoch 1043/10000
Epoch 1044/10000
Epoch 1045/10000
Epoch 1046/10000
Epoch 1047/10000
Epoch 1048/10000
Epoch 1049/10000
Epoch 1050/10000
Epoch 1051/10000
Epoch 1052/10000
Epoch 1053/10000
Epoch 1054/10000
Epoch 1055/10000
Epoch 1056/10000
Epoch 1057/10000
Epoch 1058/10000
Epoch 1059/10000
Epoch 1060/10000
Epoch 1061/10000
Epoch 1062/10000
Epoch 1063/10000
Epoch 1064/10000
Epoch 1065/10000
Epoch 1066/10000
Epoch 1067/10000
Epoch 1068/10000
Epoch 1069/10000
Epoch 1070/10000
Epoch 1071/10000
Epoch 1072/10000
Epoch 1073/10000
Epoch 1074/10000
Epoch 1075/10000
Epoch 1076/10000
Epoch 1077/10000
Epoch 1078/10000
Epoch 1079/10000
Epoch 1080/10000
Epoch 1081/10000
Epoch 1082/10000
Epoch 1083/10000
Epoch 1084/10000
Epoch 1085/10000
Epoch 1086/10000
Epoch 1087/10000
Epoch 1088/10000
Epoch 1089/10000
Epoch 1090/10000
Epoch 1091/10000
Epoch 1092/10000
Epoch 1093/10000
Epoch 1094/10000
Epoch 1095/10000
Epoch 1096/10000
Epoch 1097/10000
Epoch 1098/10000
Epoch 1099/10000
Epoch 1100/100

Epoch 1535/10000
Epoch 1536/10000
Epoch 1537/10000
Epoch 1538/10000
Epoch 1539/10000
Epoch 1540/10000
Epoch 1541/10000
Epoch 1542/10000
Epoch 1543/10000
Epoch 1544/10000
Epoch 1545/10000
Epoch 1546/10000
Epoch 1547/10000
Epoch 1548/10000
Epoch 1549/10000
Epoch 1550/10000
Epoch 1551/10000
Epoch 1552/10000
Epoch 1553/10000
Epoch 1554/10000
Epoch 1555/10000
Epoch 1556/10000
Epoch 1557/10000
Epoch 1558/10000
Epoch 1559/10000
Epoch 1560/10000
Epoch 1561/10000
Epoch 1562/10000
Epoch 1563/10000
Epoch 1564/10000
Epoch 1565/10000
Epoch 1566/10000
Epoch 1567/10000
Epoch 1568/10000
Epoch 1569/10000
Epoch 1570/10000
Epoch 1571/10000
Epoch 1572/10000
Epoch 1573/10000
Epoch 1574/10000
Epoch 1575/10000
Epoch 1576/10000
Epoch 1577/10000
Epoch 1578/10000
Epoch 1579/10000
Epoch 1580/10000
Epoch 1581/10000
Epoch 1582/10000
Epoch 1583/10000
Epoch 1584/10000
Epoch 1585/10000
Epoch 1586/10000
Epoch 1587/10000
Epoch 1588/10000
Epoch 1589/10000
Epoch 1590/10000
Epoch 1591/10000
Epoch 1592/10000
Epoch 1593/100

Epoch 2026/10000
Epoch 2027/10000
Epoch 2028/10000
Epoch 2029/10000
Epoch 2030/10000
Epoch 2031/10000
Epoch 2032/10000
Epoch 2033/10000
Epoch 2034/10000
Epoch 2035/10000
Epoch 2036/10000
Epoch 2037/10000
Epoch 2038/10000
Epoch 2039/10000
Epoch 2040/10000
Epoch 2041/10000
Epoch 2042/10000
Epoch 2043/10000
Epoch 2044/10000
Epoch 2045/10000
Epoch 2046/10000
Epoch 2047/10000
Epoch 2048/10000
Epoch 2049/10000
Epoch 2050/10000
Epoch 2051/10000
Epoch 2052/10000
Epoch 2053/10000
Epoch 2054/10000
Epoch 2055/10000
Epoch 2056/10000
Epoch 2057/10000
Epoch 2058/10000
Epoch 2059/10000
Epoch 2060/10000
Epoch 2061/10000
Epoch 2062/10000
Epoch 2063/10000
Epoch 2064/10000
Epoch 2065/10000
Epoch 2066/10000
Epoch 2067/10000
Epoch 2068/10000
Epoch 2069/10000
Epoch 2070/10000
Epoch 2071/10000
Epoch 2072/10000
Epoch 2073/10000
Epoch 2074/10000
Epoch 2075/10000
Epoch 2076/10000
Epoch 2077/10000
Epoch 2078/10000
Epoch 2079/10000
Epoch 2080/10000
Epoch 2081/10000
Epoch 2082/10000
Epoch 2083/10000
Epoch 2084/100

...

Epoch 7832/10000
Epoch 7833/10000
Epoch 7834/10000
Epoch 7835/10000
Epoch 7836/10000
Epoch 7837/10000
Epoch 7838/10000
Epoch 7839/10000
Epoch 7840/10000
Epoch 7841/10000
Epoch 7842/10000
Epoch 7843/10000
Epoch 7844/10000
Epoch 7845/10000
Epoch 7846/10000
Epoch 7847/10000
Epoch 7848/10000
Epoch 7849/10000
Epoch 7850/10000
Epoch 7851/10000
Epoch 7852/10000
Epoch 7853/10000
Epoch 7854/10000
Epoch 7855/10000
Epoch 7856/10000
Epoch 7857/10000
Epoch 7858/10000
Epoch 7859/10000
Epoch 7860/10000
Epoch 7861/10000
Epoch 7862/10000
Epoch 7863/10000
Epoch 7864/10000
Epoch 7865/10000
Epoch 7866/10000
Epoch 7867/10000
Epoch 7868/10000
Epoch 7869/10000
Epoch 7870/10000
Epoch 7871/10000
Epoch 7872/10000
Epoch 7873/10000
Epoch 7874/10000
Epoch 7875/10000
Epoch 7876/10000
Epoch 7877/10000
Epoch 7878/10000
Epoch 7879/10000
Epoch 7880/10000
Epoch 7881/10000
Epoch 7882/10000
Epoch 7883/10000
Epoch 7884/10000
Epoch 7885/10000
Epoch 7886/10000
Epoch 7887/10000
Epoch 7888/10000
Epoch 7889/10000
Epoch 7890/100

Epoch 8323/10000
Epoch 8324/10000
Epoch 8325/10000
Epoch 8326/10000
Epoch 8327/10000
Epoch 8328/10000
Epoch 8329/10000
Epoch 8330/10000
Epoch 8331/10000
Epoch 8332/10000
Epoch 8333/10000
Epoch 8334/10000
Epoch 8335/10000
Epoch 8336/10000
Epoch 8337/10000
Epoch 8338/10000
Epoch 8339/10000
Epoch 8340/10000
Epoch 8341/10000
Epoch 8342/10000
Epoch 8343/10000
Epoch 8344/10000
Epoch 8345/10000
Epoch 8346/10000
Epoch 8347/10000
Epoch 8348/10000
Epoch 8349/10000
Epoch 8350/10000
Epoch 8351/10000
Epoch 8352/10000
Epoch 8353/10000
Epoch 8354/10000
Epoch 8355/10000
Epoch 8356/10000
Epoch 8357/10000
Epoch 8358/10000
Epoch 8359/10000
Epoch 8360/10000
Epoch 8361/10000
Epoch 8362/10000
Epoch 8363/10000
Epoch 8364/10000
Epoch 8365/10000
Epoch 8366/10000
Epoch 8367/10000
Epoch 8368/10000
Epoch 8369/10000
Epoch 8370/10000
Epoch 8371/10000
Epoch 8372/10000
Epoch 8373/10000
Epoch 8374/10000
Epoch 8375/10000
Epoch 8376/10000
Epoch 8377/10000
Epoch 8378/10000
Epoch 8379/10000
Epoch 8380/10000
Epoch 8381/100

Epoch 8816/10000
Epoch 8817/10000
Epoch 8818/10000
Epoch 8819/10000
Epoch 8820/10000
Epoch 8821/10000
Epoch 8822/10000
Epoch 8823/10000
Epoch 8824/10000
Epoch 8825/10000
Epoch 8826/10000
Epoch 8827/10000
Epoch 8828/10000
Epoch 8829/10000
Epoch 8830/10000
Epoch 8831/10000
Epoch 8832/10000
Epoch 8833/10000
Epoch 8834/10000
Epoch 8835/10000
Epoch 8836/10000
Epoch 8837/10000
Epoch 8838/10000
Epoch 8839/10000
Epoch 8840/10000
Epoch 8841/10000
Epoch 8842/10000
Epoch 8843/10000
Epoch 8844/10000
Epoch 8845/10000
Epoch 8846/10000
Epoch 8847/10000
Epoch 8848/10000
Epoch 8849/10000
Epoch 8850/10000
Epoch 8851/10000
Epoch 8852/10000
Epoch 8853/10000
Epoch 8854/10000
Epoch 8855/10000
Epoch 8856/10000
Epoch 8857/10000
Epoch 8858/10000
Epoch 8859/10000
Epoch 8860/10000
Epoch 8861/10000
Epoch 8862/10000
Epoch 8863/10000
Epoch 8864/10000
Epoch 8865/10000
Epoch 8866/10000
Epoch 8867/10000
Epoch 8868/10000
Epoch 8869/10000
Epoch 8870/10000
Epoch 8871/10000
Epoch 8872/10000
Epoch 8873/10000
Epoch 8874/100

Epoch 9307/10000
Epoch 9308/10000
Epoch 9309/10000
Epoch 9310/10000
Epoch 9311/10000
Epoch 9312/10000
Epoch 9313/10000
Epoch 9314/10000
Epoch 9315/10000
Epoch 9316/10000
Epoch 9317/10000
Epoch 9318/10000
Epoch 9319/10000
Epoch 9320/10000
Epoch 9321/10000
Epoch 9322/10000
Epoch 9323/10000
Epoch 9324/10000
Epoch 9325/10000
Epoch 9326/10000
Epoch 9327/10000
Epoch 9328/10000
Epoch 9329/10000
Epoch 9330/10000
Epoch 9331/10000
Epoch 9332/10000
Epoch 9333/10000
Epoch 9334/10000
Epoch 9335/10000
Epoch 9336/10000
Epoch 9337/10000
Epoch 9338/10000
Epoch 9339/10000
Epoch 9340/10000
Epoch 9341/10000
Epoch 9342/10000
Epoch 9343/10000
Epoch 9344/10000
Epoch 9345/10000
Epoch 9346/10000
Epoch 9347/10000
Epoch 9348/10000
Epoch 9349/10000
Epoch 9350/10000
Epoch 9351/10000
Epoch 9352/10000
Epoch 9353/10000
Epoch 9354/10000
Epoch 9355/10000
Epoch 9356/10000
Epoch 9357/10000
Epoch 9358/10000
Epoch 9359/10000
Epoch 9360/10000
Epoch 9361/10000
Epoch 9362/10000
Epoch 9363/10000
Epoch 9364/10000
Epoch 9365/100

Epoch 9803/10000
Epoch 9804/10000
Epoch 9805/10000
Epoch 9806/10000
Epoch 9807/10000
Epoch 9808/10000
Epoch 9809/10000
Epoch 9810/10000
Epoch 9811/10000
Epoch 9812/10000
Epoch 9813/10000
Epoch 9814/10000
Epoch 9815/10000
Epoch 9816/10000
Epoch 9817/10000
Epoch 9818/10000
Epoch 9819/10000
Epoch 9820/10000
Epoch 9821/10000
Epoch 9822/10000
Epoch 9823/10000
Epoch 9824/10000
Epoch 9825/10000
Epoch 9826/10000
Epoch 9827/10000
Epoch 9828/10000
Epoch 9829/10000
Epoch 9830/10000
Epoch 9831/10000
Epoch 9832/10000
Epoch 9833/10000
Epoch 9834/10000
Epoch 9835/10000
Epoch 9836/10000
Epoch 9837/10000
Epoch 9838/10000
Epoch 9839/10000
Epoch 9840/10000
Epoch 9841/10000
Epoch 9842/10000
Epoch 9843/10000
Epoch 9844/10000
Epoch 9845/10000
Epoch 9846/10000
Epoch 9847/10000
Epoch 9848/10000
Epoch 9849/10000
Epoch 9850/10000
Epoch 9851/10000
Epoch 9852/10000
Epoch 9853/10000
Epoch 9854/10000
Epoch 9855/10000
Epoch 9856/10000
Epoch 9857/10000
Epoch 9858/10000
Epoch 9859/10000
Epoch 9860/10000
Epoch 9861/100

In [47]:
ss['index']

0       26457
1       26458
2       26459
3       26460
4       26461
        ...  
9995    36452
9996    36453
9997    36454
9998    36455
9999    36456
Name: index, Length: 10000, dtype: int64

In [50]:
df_nn = pd.DataFrame(nn)
ss.iloc[:,1:] = df_nn
ss.to_csv('nn.csv',index=False)

In [25]:
xg = np.zeros((10000,3))
xgboost = XGBClassifier(tree_method = "gpu_hist",
                        n_estimators = 700,
                        max_depth = 25,
                        learning_rate= 0.1,
                        min_child_weight = 2,
                        subsample = 0.85,
                        colsample_bytree = 0.31,
                        gamma = 0,
                        max_delta_step = 0.07,
                        nthread = -1,
                        eval_metric = 'mlogloss')
for i, (train_idx, valid_idx) in enumerate(skf.split(X,y)):    
    
    X_train, y_train = X.iloc[train_idx,:], y[train_idx]
    X_valid, y_valid = X.iloc[valid_idx,:], y[valid_idx]
    
    xgboost.fit(X_train,y_train,
               eval_set = [(X_valid,y_valid)])
    
    xg += xgboost.predict_proba(test)/10

[0]	validation_0-mlogloss:1.09318
[1]	validation_0-mlogloss:1.08774
[2]	validation_0-mlogloss:1.08237
[3]	validation_0-mlogloss:1.07698
[4]	validation_0-mlogloss:1.07169
[5]	validation_0-mlogloss:1.06644
[6]	validation_0-mlogloss:1.06123
[7]	validation_0-mlogloss:1.05610
[8]	validation_0-mlogloss:1.05094
[9]	validation_0-mlogloss:1.04593
[10]	validation_0-mlogloss:1.04092
[11]	validation_0-mlogloss:1.03592
[12]	validation_0-mlogloss:1.03100
[13]	validation_0-mlogloss:1.02609
[14]	validation_0-mlogloss:1.02126
[15]	validation_0-mlogloss:1.01650
[16]	validation_0-mlogloss:1.01180
[17]	validation_0-mlogloss:1.00709
[18]	validation_0-mlogloss:1.00240
[19]	validation_0-mlogloss:0.99770
[20]	validation_0-mlogloss:0.99316
[21]	validation_0-mlogloss:0.98874
[22]	validation_0-mlogloss:0.98414
[23]	validation_0-mlogloss:0.97977
[24]	validation_0-mlogloss:0.97534
[25]	validation_0-mlogloss:0.97093
[26]	validation_0-mlogloss:0.96661
[27]	validation_0-mlogloss:0.96223
[28]	validation_0-mlogloss:0.9

[231]	validation_0-mlogloss:0.72077
[232]	validation_0-mlogloss:0.72074
[233]	validation_0-mlogloss:0.72070
[234]	validation_0-mlogloss:0.72061
[235]	validation_0-mlogloss:0.72058
[236]	validation_0-mlogloss:0.72044
[237]	validation_0-mlogloss:0.72040
[238]	validation_0-mlogloss:0.72031
[239]	validation_0-mlogloss:0.72028
[240]	validation_0-mlogloss:0.72030
[241]	validation_0-mlogloss:0.72023
[242]	validation_0-mlogloss:0.72014
[243]	validation_0-mlogloss:0.72012
[244]	validation_0-mlogloss:0.72008
[245]	validation_0-mlogloss:0.72008
[246]	validation_0-mlogloss:0.72003
[247]	validation_0-mlogloss:0.71990
[248]	validation_0-mlogloss:0.71977
[249]	validation_0-mlogloss:0.71970
[250]	validation_0-mlogloss:0.71975
[251]	validation_0-mlogloss:0.71970
[252]	validation_0-mlogloss:0.71967
[253]	validation_0-mlogloss:0.71959
[254]	validation_0-mlogloss:0.71955
[255]	validation_0-mlogloss:0.71953
[256]	validation_0-mlogloss:0.71946
[257]	validation_0-mlogloss:0.71940
[258]	validation_0-mlogloss:

[459]	validation_0-mlogloss:0.71802
[460]	validation_0-mlogloss:0.71801
[461]	validation_0-mlogloss:0.71799
[462]	validation_0-mlogloss:0.71797
[463]	validation_0-mlogloss:0.71797
[464]	validation_0-mlogloss:0.71796
[465]	validation_0-mlogloss:0.71796
[466]	validation_0-mlogloss:0.71795
[467]	validation_0-mlogloss:0.71795
[468]	validation_0-mlogloss:0.71797
[469]	validation_0-mlogloss:0.71797
[470]	validation_0-mlogloss:0.71801
[471]	validation_0-mlogloss:0.71802
[472]	validation_0-mlogloss:0.71802
[473]	validation_0-mlogloss:0.71803
[474]	validation_0-mlogloss:0.71807
[475]	validation_0-mlogloss:0.71812
[476]	validation_0-mlogloss:0.71813
[477]	validation_0-mlogloss:0.71812
[478]	validation_0-mlogloss:0.71818
[479]	validation_0-mlogloss:0.71822
[480]	validation_0-mlogloss:0.71822
[481]	validation_0-mlogloss:0.71821
[482]	validation_0-mlogloss:0.71827
[483]	validation_0-mlogloss:0.71827
[484]	validation_0-mlogloss:0.71830
[485]	validation_0-mlogloss:0.71833
[486]	validation_0-mlogloss:

[687]	validation_0-mlogloss:0.71987
[688]	validation_0-mlogloss:0.71988
[689]	validation_0-mlogloss:0.71989
[690]	validation_0-mlogloss:0.71994
[691]	validation_0-mlogloss:0.71989
[692]	validation_0-mlogloss:0.71987
[693]	validation_0-mlogloss:0.71989
[694]	validation_0-mlogloss:0.71992
[695]	validation_0-mlogloss:0.71993
[696]	validation_0-mlogloss:0.71993
[697]	validation_0-mlogloss:0.71996
[698]	validation_0-mlogloss:0.71995
[699]	validation_0-mlogloss:0.71994
[0]	validation_0-mlogloss:1.09311
[1]	validation_0-mlogloss:1.08759
[2]	validation_0-mlogloss:1.08211
[3]	validation_0-mlogloss:1.07665
[4]	validation_0-mlogloss:1.07123
[5]	validation_0-mlogloss:1.06596
[6]	validation_0-mlogloss:1.06064
[7]	validation_0-mlogloss:1.05536
[8]	validation_0-mlogloss:1.05012
[9]	validation_0-mlogloss:1.04494
[10]	validation_0-mlogloss:1.03986
[11]	validation_0-mlogloss:1.03474
[12]	validation_0-mlogloss:1.02967
[13]	validation_0-mlogloss:1.02460
[14]	validation_0-mlogloss:1.01972
[15]	validation_0

[218]	validation_0-mlogloss:0.71338
[219]	validation_0-mlogloss:0.71335
[220]	validation_0-mlogloss:0.71331
[221]	validation_0-mlogloss:0.71329
[222]	validation_0-mlogloss:0.71328
[223]	validation_0-mlogloss:0.71327
[224]	validation_0-mlogloss:0.71317
[225]	validation_0-mlogloss:0.71309
[226]	validation_0-mlogloss:0.71301
[227]	validation_0-mlogloss:0.71298
[228]	validation_0-mlogloss:0.71297
[229]	validation_0-mlogloss:0.71292
[230]	validation_0-mlogloss:0.71299
[231]	validation_0-mlogloss:0.71293
[232]	validation_0-mlogloss:0.71287
[233]	validation_0-mlogloss:0.71279
[234]	validation_0-mlogloss:0.71276
[235]	validation_0-mlogloss:0.71271
[236]	validation_0-mlogloss:0.71260
[237]	validation_0-mlogloss:0.71255
[238]	validation_0-mlogloss:0.71247
[239]	validation_0-mlogloss:0.71243
[240]	validation_0-mlogloss:0.71240
[241]	validation_0-mlogloss:0.71232
[242]	validation_0-mlogloss:0.71225
[243]	validation_0-mlogloss:0.71220
[244]	validation_0-mlogloss:0.71219
[245]	validation_0-mlogloss:

...

[355]	validation_0-mlogloss:0.73184
[356]	validation_0-mlogloss:0.73182
[357]	validation_0-mlogloss:0.73182
[358]	validation_0-mlogloss:0.73184
[359]	validation_0-mlogloss:0.73184
[360]	validation_0-mlogloss:0.73179
[361]	validation_0-mlogloss:0.73173
[362]	validation_0-mlogloss:0.73171
[363]	validation_0-mlogloss:0.73172
[364]	validation_0-mlogloss:0.73171
[365]	validation_0-mlogloss:0.73168
[366]	validation_0-mlogloss:0.73170
[367]	validation_0-mlogloss:0.73163
[368]	validation_0-mlogloss:0.73166
[369]	validation_0-mlogloss:0.73169
[370]	validation_0-mlogloss:0.73174
[371]	validation_0-mlogloss:0.73178
[372]	validation_0-mlogloss:0.73180
[373]	validation_0-mlogloss:0.73181
[374]	validation_0-mlogloss:0.73178
[375]	validation_0-mlogloss:0.73178
[376]	validation_0-mlogloss:0.73184
[377]	validation_0-mlogloss:0.73185
[378]	validation_0-mlogloss:0.73187
[379]	validation_0-mlogloss:0.73192
[380]	validation_0-mlogloss:0.73194
[381]	validation_0-mlogloss:0.73203
[382]	validation_0-mlogloss:

[583]	validation_0-mlogloss:0.73500
[584]	validation_0-mlogloss:0.73505
[585]	validation_0-mlogloss:0.73507
[586]	validation_0-mlogloss:0.73510
[587]	validation_0-mlogloss:0.73506
[588]	validation_0-mlogloss:0.73503
[589]	validation_0-mlogloss:0.73508
[590]	validation_0-mlogloss:0.73508
[591]	validation_0-mlogloss:0.73510
[592]	validation_0-mlogloss:0.73522
[593]	validation_0-mlogloss:0.73525
[594]	validation_0-mlogloss:0.73523
[595]	validation_0-mlogloss:0.73523
[596]	validation_0-mlogloss:0.73526
[597]	validation_0-mlogloss:0.73531
[598]	validation_0-mlogloss:0.73531
[599]	validation_0-mlogloss:0.73536
[600]	validation_0-mlogloss:0.73531
[601]	validation_0-mlogloss:0.73531
[602]	validation_0-mlogloss:0.73530
[603]	validation_0-mlogloss:0.73527
[604]	validation_0-mlogloss:0.73526
[605]	validation_0-mlogloss:0.73528
[606]	validation_0-mlogloss:0.73523
[607]	validation_0-mlogloss:0.73517
[608]	validation_0-mlogloss:0.73515
[609]	validation_0-mlogloss:0.73514
[610]	validation_0-mlogloss:

[114]	validation_0-mlogloss:0.74558
[115]	validation_0-mlogloss:0.74448
[116]	validation_0-mlogloss:0.74372
[117]	validation_0-mlogloss:0.74272
[118]	validation_0-mlogloss:0.74200
[119]	validation_0-mlogloss:0.74133
[120]	validation_0-mlogloss:0.74055
[121]	validation_0-mlogloss:0.73981
[122]	validation_0-mlogloss:0.73912
[123]	validation_0-mlogloss:0.73851
[124]	validation_0-mlogloss:0.73787
[125]	validation_0-mlogloss:0.73720
[126]	validation_0-mlogloss:0.73654
[127]	validation_0-mlogloss:0.73607
[128]	validation_0-mlogloss:0.73554
[129]	validation_0-mlogloss:0.73508
[130]	validation_0-mlogloss:0.73445
[131]	validation_0-mlogloss:0.73394
[132]	validation_0-mlogloss:0.73336
[133]	validation_0-mlogloss:0.73278
[134]	validation_0-mlogloss:0.73237
[135]	validation_0-mlogloss:0.73191
[136]	validation_0-mlogloss:0.73162
[137]	validation_0-mlogloss:0.73127
[138]	validation_0-mlogloss:0.73098
[139]	validation_0-mlogloss:0.73072
[140]	validation_0-mlogloss:0.73029
[141]	validation_0-mlogloss:

[342]	validation_0-mlogloss:0.71843
[343]	validation_0-mlogloss:0.71837
[344]	validation_0-mlogloss:0.71836
[345]	validation_0-mlogloss:0.71836
[346]	validation_0-mlogloss:0.71838
[347]	validation_0-mlogloss:0.71835
[348]	validation_0-mlogloss:0.71835
[349]	validation_0-mlogloss:0.71837
[350]	validation_0-mlogloss:0.71841
[351]	validation_0-mlogloss:0.71842
[352]	validation_0-mlogloss:0.71842
[353]	validation_0-mlogloss:0.71842
[354]	validation_0-mlogloss:0.71841
[355]	validation_0-mlogloss:0.71842
[356]	validation_0-mlogloss:0.71847
[357]	validation_0-mlogloss:0.71847
[358]	validation_0-mlogloss:0.71852
[359]	validation_0-mlogloss:0.71847
[360]	validation_0-mlogloss:0.71843
[361]	validation_0-mlogloss:0.71841
[362]	validation_0-mlogloss:0.71839
[363]	validation_0-mlogloss:0.71841
[364]	validation_0-mlogloss:0.71843
[365]	validation_0-mlogloss:0.71842
[366]	validation_0-mlogloss:0.71842
[367]	validation_0-mlogloss:0.71838
[368]	validation_0-mlogloss:0.71840
[369]	validation_0-mlogloss:

[570]	validation_0-mlogloss:0.72122
[571]	validation_0-mlogloss:0.72125
[572]	validation_0-mlogloss:0.72121
[573]	validation_0-mlogloss:0.72121
[574]	validation_0-mlogloss:0.72122
[575]	validation_0-mlogloss:0.72123
[576]	validation_0-mlogloss:0.72123
[577]	validation_0-mlogloss:0.72124
[578]	validation_0-mlogloss:0.72127
[579]	validation_0-mlogloss:0.72127
[580]	validation_0-mlogloss:0.72131
[581]	validation_0-mlogloss:0.72132
[582]	validation_0-mlogloss:0.72134
[583]	validation_0-mlogloss:0.72137
[584]	validation_0-mlogloss:0.72135
[585]	validation_0-mlogloss:0.72137
[586]	validation_0-mlogloss:0.72140
[587]	validation_0-mlogloss:0.72140
[588]	validation_0-mlogloss:0.72141
[589]	validation_0-mlogloss:0.72140
[590]	validation_0-mlogloss:0.72147
[591]	validation_0-mlogloss:0.72150
[592]	validation_0-mlogloss:0.72152
[593]	validation_0-mlogloss:0.72150
[594]	validation_0-mlogloss:0.72153
[595]	validation_0-mlogloss:0.72157
[596]	validation_0-mlogloss:0.72158
[597]	validation_0-mlogloss:

In [30]:
pd.DataFrame(nn)

array([[0.07805516, 0.12964418, 0.79230065],
       [0.59987119, 0.09780917, 0.30231967],
       [0.07805516, 0.12964418, 0.79230065],
       ...,
       [0.07319259, 0.12069604, 0.80611136],
       [0.09381481, 0.33444604, 0.57173917],
       [0.09381481, 0.33444604, 0.57173917]])

In [27]:
weight_xg = 0.5
weight_nn = 0.5


ss = pd.read_csv(d + '\\' +'sample_submission.csv')
ss.iloc[:,1:]=0
ss.iloc[:,1:] += (weight_xg * xg) + (weight_nn * nn)

In [28]:
ss

index         0         1         2
0     26457  0.078232  0.128635  0.793133
1     26458  0.632587  0.094967  0.272446
2     26459  0.078232  0.128635  0.793133
3     26460  0.078232  0.128635  0.793133
4     26461  0.083866  0.309060  0.607073
...     ...       ...       ...       ...
9995  36452  0.078232  0.128635  0.793133
9996  36453  0.048462  0.476890  0.474648
9997  36454  0.075977  0.117776  0.806247
9998  36455  0.106594  0.326225  0.567181
9999  36456  0.106594  0.326225  0.567181

[10000 rows x 4 columns]

In [29]:
y

0        1.0
1        1.0
2        2.0
3        0.0
4        2.0
        ... 
26452    1.0
26453    2.0
26454    2.0
26455    2.0
26456    2.0
Name: credit, Length: 26457, dtype: float64

In [ ]:
ss.to_csv('test.csv', index=False)